In [1]:
# !pip install plotly kaleido datasets nbformat -U -q

In [2]:
import os

import datasets
import pandas as pd
from dotenv import load_dotenv
from huggingface_hub import login


load_dotenv(override=True)
login(os.getenv("HF_TOKEN"))

pd.set_option("max_colwidth", None)

OUTPUT_DIR = "output"

/Users/aymeric/venv/gaia/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Note: Environment variable`HF_TOKEN` is set and is the current active token independently from the token you've just configured.


In [3]:
eval_ds = datasets.load_dataset("gaia-benchmark/GAIA", "2023_all")["validation"]
eval_ds = eval_ds.rename_columns({"Question": "question", "Final answer": "true_answer", "Level": "task"})
eval_df = pd.DataFrame(eval_ds)

In [4]:
pd.Series(eval_ds["task"]).value_counts()

2    86
1    53
3    26
Name: count, dtype: int64

# 1. Load all results

In [5]:
import glob


results = []
for f in glob.glob(f"{OUTPUT_DIR}/validation/*.jsonl"):
    df = pd.read_json(f, lines=True)
    df["agent_name"] = f.split("/")[-1].split(".")[0]
    results.append(df)

result_df = pd.concat(results)
result_df = result_df.drop(columns=["start_time", "end_time"])
result_df["prediction"] = result_df["prediction"].fillna("No prediction")

In [6]:
import re
from collections import Counter

from scripts.gaia_scorer import check_close_call, question_scorer


result_df["is_correct"] = result_df.apply(lambda x: question_scorer(x["prediction"], x["true_answer"]), axis=1)
result_df["is_near_correct"] = result_df.apply(
    lambda x: check_close_call(x["prediction"], x["true_answer"], x["is_correct"]),
    axis=1,
)

result_df["count_steps"] = result_df["intermediate_steps"].apply(len)


def find_attachment(question):
    matches = eval_df.loc[eval_df["question"].apply(lambda x: x in question), "file_name"]

    if len(matches) == 0:
        return "Not found"
    file_path = matches.values[0]

    if isinstance(file_path, str) and len(file_path) > 0:
        return file_path.split(".")[-1]
    else:
        return "None"


result_df["attachment_type"] = result_df["question"].apply(find_attachment)


def extract_tool_calls(code):
    regex = r"\b(\w+)\("
    function_calls = [el for el in re.findall(regex, code) if el.islower()]

    function_call_counter = Counter(function_calls)
    return function_call_counter


def sum_tool_calls(steps):
    total_count = Counter()
    for step in steps:
        if "llm_output" in step:
            total_count += extract_tool_calls(step["llm_output"])

    return total_count


# result_df["tool_calls"] = result_df["intermediate_steps"].apply(sum_tool_calls)

/Users/aymeric/Documents/Code/smolagents/examples/open_deep_research/scripts/gaia_scorer.py:52: UserWarning: Answer lists have different lengths, returning False.
  warnings.warn("Answer lists have different lengths, returning False.", UserWarning)


String Unable to determine cannot be normalized to number str.
String Unable to determine cannot be normalized to number str.
String No prediction cannot be normalized to number str.
String 2 High fantasy A Song of Ice and Fire cannot be normalized to number str.
String  cannot be normalized to number str.
String 94 CFM for Cheater cannot be normalized to number str.
String  93 CFM for Cheater beater cannot be normalized to number str.
String No prediction cannot be normalized to number str.
String 2017 Komo Mai Drive 900000 cannot be normalized to number str.
String No prediction cannot be normalized to number str.
String Unable to determine cannot be normalized to number str.
String No prediction cannot be normalized to number str.
String Unable to determine cannot be normalized to number str.
String No prediction cannot be normalized to number str.
String Unable to determine cannot be normalized to number str.
String No prediction cannot be normalized to number str.
String No predic

In [7]:
def get_thoughts(x):
    try:
        output = x[0]["task"]
        for y in x[1:]:
            try:
                if "observation" in y:
                    output += y["llm_output"] + "\nObservation:" + y["observation"]
                else:
                    output += y["llm_output"] + r"\Error:" + str(y["error"])
            except Exception:
                pass
        return output
    except Exception:
        return None


result_df["thoughts"] = result_df["intermediate_steps"].apply(lambda x: get_thoughts(x))

In [8]:
result_df["agent_name"].value_counts()

agent_name
code_o3-mini_03_february_remove-navigational      165
code_o1_03_february_text_high-reasoning-effort    165
code_o1_01_february_text                          165
code_gpt4o_03_february_text                       165
code_o1_03_february_fix-print-outputs             164
code_o1_03_february_remove-navigational           164
code_o1_03_february_goodoldtext-unbroken          161
code_gpt4o_03_february_magenticbrowser            159
code_gpt4o_03_february_goodoldtext-unbroken       159
code_o1_03_february_fix-print-outputs2            156
code_gpt4o_03_february_magenticbrowser2           156
code_o1_29-01_text                                105
code_llama-3                                       90
code_o1_22-01_managedagent-summary_planning        67
code_o1_25-01_visioon                              53
code_gpt4o_03_february_goodoldtext                 50
code_qwen-coder-32B_03_february_text               43
code_sonnet_03_february_goodoldtext-unbroken        1
Name: count, dtyp

# 2. Inspect specific runs

In [9]:
o1_vision = "code_o1_25-01_visioon"
o1_next = "code_o1_29-01_text"
o1 = "code_o1_01_february_text"

list_versions = [o1, o1_vision, o1_next]

# submission_selection_name = "react_code_llama3-70b_02-05_full-gaia-validation-code"
sel_df = result_df
# sel_df = sel_df.loc[
#     (result_df["agent_name"].isin(list_versions))
#     # & (~result_df["question"].isin(UNSOLVED_QUESTIONS))
# ]
sel_df = sel_df.reset_index(drop=True)
display(sel_df["agent_name"].value_counts())
sel_df = sel_df.drop_duplicates(subset=["agent_name", "question"])
display(sel_df.groupby("agent_name")[["task"]].value_counts())
print("Total length:", len(sel_df), "- is complete:", len(sel_df) == 165)
# assert sel_df["question"].value_counts().max() == len(list_versions), "Some questions are duplicate!"

agent_name
code_o3-mini_03_february_remove-navigational      165
code_o1_03_february_text_high-reasoning-effort    165
code_o1_01_february_text                          165
code_gpt4o_03_february_text                       165
code_o1_03_february_fix-print-outputs             164
code_o1_03_february_remove-navigational           164
code_o1_03_february_goodoldtext-unbroken          161
code_gpt4o_03_february_magenticbrowser            159
code_gpt4o_03_february_goodoldtext-unbroken       159
code_o1_03_february_fix-print-outputs2            156
code_gpt4o_03_february_magenticbrowser2           156
code_o1_29-01_text                                105
code_llama-3                                       90
code_o1_22-01_managedagent-summary_planning        67
code_o1_25-01_visioon                              53
code_gpt4o_03_february_goodoldtext                 50
code_qwen-coder-32B_03_february_text               43
code_sonnet_03_february_goodoldtext-unbroken        1
Name: count, dtyp

agent_name                                      task
code_gpt4o_03_february_goodoldtext              2       26
                                                1       19
                                                3        5
code_gpt4o_03_february_goodoldtext-unbroken     2       84
                                                1       53
                                                3       22
code_gpt4o_03_february_magenticbrowser          2       83
                                                1       52
                                                3       24
code_gpt4o_03_february_magenticbrowser2         2       81
                                                1       52
                                                3       23
code_gpt4o_03_february_text                     2       86
                                                1       53
                                                3       26
code_llama-3                                    2       50
   

Total length: 2188 - is complete: False


In [10]:
display("Average score:", sel_df.groupby("agent_name")[["is_correct"]].mean().round(3))
display(
    sel_df.groupby(["agent_name", "task"])[["is_correct", "is_near_correct", "count_steps", "question"]]
    .agg(
        {
            "is_correct": "mean",
            "is_near_correct": "mean",
            "count_steps": "mean",
            "question": "count",
        }
    )
    .rename(columns={"question": "count"})
)

'Average score:'

is_correct
agent_name                                                
code_gpt4o_03_february_goodoldtext                   0.440
code_gpt4o_03_february_goodoldtext-unbroken          0.384
code_gpt4o_03_february_magenticbrowser               0.352
code_gpt4o_03_february_magenticbrowser2              0.365
code_gpt4o_03_february_text                          0.376
code_llama-3                                         0.078
code_o1_01_february_text                             0.491
code_o1_03_february_fix-print-outputs                0.518
code_o1_03_february_fix-print-outputs2               0.526
code_o1_03_february_goodoldtext-unbroken             0.534
code_o1_03_february_remove-navigational              0.537
code_o1_03_february_text_high-reasoning-effort       0.485
code_o1_22-01_managedagent-summary_planning          0.418
code_o1_25-01_visioon                                0.340
code_o1_29-01_text                                   0.390
code_o3-mini_03_february_remove-navigational         0.291
code_qwen-coder-32B_03_february_text                 0.209
code_sonnet_03_february_goodoldtext-unbroken         0.000

is_correct  \
agent_name                                     task               
code_gpt4o_03_february_goodoldtext             1       0.631579   
                                               2       0.346154   
                                               3       0.200000   
code_gpt4o_03_february_goodoldtext-unbroken    1       0.452830   
                                               2       0.380952   
                                               3       0.227273   
code_gpt4o_03_february_magenticbrowser         1       0.480769   
                                               2       0.349398   
                                               3       0.083333   
code_gpt4o_03_february_magenticbrowser2        1       0.461538   
                                               2       0.345679   
                                               3       0.217391   
code_gpt4o_03_february_text                    1       0.433962   
                                               2       0.406977   
                                               3       0.153846   
code_llama-3                                   1       0.192308   
                                               2       0.040000   
                                               3       0.000000   
code_o1_01_february_text                       1       0.547170   
                                               2       0.534884   
                                               3       0.230769   
code_o1_03_february_fix-print-outputs          1       0.622642   
                                               2       0.505882   
                                               3       0.346154   
code_o1_03_february_fix-print-outputs2         1       0.641509   
                                               2       0.506329   
                                               3       0.333333   
code_o1_03_february_goodoldtext-unbroken       1       0.622642   
                                               2       0.541176   
                                               3       0.304348   
code_o1_03_february_remove-navigational        1       0.641509   
                                               2       0.541176   
                                               3       0.307692   
code_o1_03_february_text_high-reasoning-effort 1       0.547170   
                                               2       0.523256   
                                               3       0.230769   
code_o1_22-01_managedagent-summary_planning    1       0.476190   
                                               2       0.472222   
                                               3       0.100000   
code_o1_25-01_visioon                          1       0.411765   
                                               2       0.366667   
                                               3       0.000000   
code_o1_29-01_text                             1       0.516129   
                                               2       0.379310   
                                               3       0.187500   
code_o3-mini_03_february_remove-navigational   1       0.452830   
                                               2       0.232558   
                                               3       0.153846   
code_qwen-coder-32B_03_february_text           1       0.357143   
                                               2       0.136364   
                                               3       0.142857   
code_sonnet_03_february_goodoldtext-unbroken   2       0.000000   

                                                     is_near_correct  \
agent_name                                     task                    
code_gpt4o_03_february_goodoldtext             1            0.631579   
                                               2            0.384615   
                                               3            0.200000   
code_gpt4o_03_february_goodoldtext-unbroken    1            0.452830   
  

In [11]:
import plotly.express as px


cumulative_df = (
    (
        sel_df.groupby("agent_name")[["is_correct", "is_near_correct"]]
        .expanding(min_periods=1, axis=0, method="single")
        .agg({"is_correct": "mean", "is_near_correct": "count"})
        .reset_index()
    )
    .copy()
    .rename(columns={"is_near_correct": "index"})
)
cumulative_df["index"] = cumulative_df["index"].astype(int) - 1


def find_question(row):
    try:
        res = sel_df.loc[sel_df["agent_name"] == row["agent_name"], "question"].iloc[row["index"]][:50]
        return res
    except Exception:
        return ""


cumulative_df["question"] = cumulative_df.apply(find_question, axis=1)
# cumulative_df["question"] = [el[:50] for el in sel_df["question"].values]

# cumulative_df["is_correct"] = cumulative_df["is_correct"] * (165 - 68) / 165

px.line(
    cumulative_df,
    color="agent_name",
    x="index",
    y="is_correct",
    hover_data="question",
)

# 3. Dive deeper into one run

In [12]:
sel_df = result_df.loc[result_df["agent_name"] == o1]
print(len(sel_df))

165


### Count errors

In [13]:
import numpy as np


error_types = [
    "AgentParsingError",
    "AgentExecutionError",
    "AgentMaxIterationsError",
    "AgentGenerationError",
]
sel_df[error_types] = 0
sel_df["Count steps"] = np.nan


def count_errors(row):
    if isinstance(row["intermediate_steps"], list):
        row["Count steps"] = len(row["intermediate_steps"])
        for step in row["intermediate_steps"]:
            if isinstance(step, dict) and "error" in step:
                try:
                    row[str(step["error"]["error_type"])] += 1
                except Exception:
                    pass
    return row


sel_df = sel_df.apply(count_errors, axis=1)

/var/folders/6m/9b1tts6d5w960j80wbw9tx3m0000gn/T/ipykernel_94354/2022001392.py:10: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/6m/9b1tts6d5w960j80wbw9tx3m0000gn/T/ipykernel_94354/2022001392.py:10: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/6m/9b1tts6d5w960j80wbw9tx3m0000gn/T/ipykernel_94354/2022001392.py:10: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in th

In [14]:
import plotly.express as px


aggregate_errors = (
    sel_df.groupby(["is_correct"])[error_types + ["Count steps"]].mean().reset_index().melt(id_vars=["is_correct"])
)

fig = px.bar(
    aggregate_errors,
    y="value",
    x="variable",
    color="is_correct",
    labels={
        "agent_name": "<b>Model</b>",
        "task": "<b>Level</b>",
        "aggregate_score": "<b>Performance</b>",
        "value": "<b>Average count</b>",
        "eval_score_GPT4": "<b>Score</b>",
    },
)
fig.update_layout(
    height=500,
    width=800,
    barmode="group",
    bargroupgap=0.0,
)
fig.update_traces(textposition="outside")
fig.write_image("aggregate_errors.png", scale=3)
fig.show()

### Inspect result by file extension type

In [15]:
display(
    sel_df.groupby(["agent_name", "attachment_type"])[["is_correct", "count_steps", "question"]].agg(
        {"is_correct": "mean", "count_steps": "mean", "question": "count"}
    )
)

is_correct  count_steps  question
agent_name               attachment_type                                   
code_o1_01_february_text None               0.496063     3.362205       127
                         csv                0.000000     7.000000         1
                         docx               1.000000     3.000000         1
                         jpg                0.000000     3.000000         2
                         jsonld             0.000000     8.000000         1
                         mp3                0.333333     2.333333         3
                         pdb                0.000000     4.000000         1
                         pdf                0.666667     2.666667         3
                         png                0.250000     2.375000         8
                         pptx               1.000000     3.000000         1
                         py                 1.000000     3.000000         1
                         txt                1.000000     4.000000         1
                         xlsx               0.615385     3.153846        13
                         zip                0.500000     4.000000         2

# 4. Ensembling methods

In [16]:
counts = result_df["agent_name"].value_counts()
long_series = result_df.loc[result_df["agent_name"].isin(counts[counts > 140].index)]

In [17]:
def majority_vote(df):
    df = df[(df["prediction"] != "Unable to determine") & (~df["prediction"].isna()) & (df["prediction"] != "None")]

    # First get the mode (most common answer) for each question
    answer_modes = df.groupby("question")["prediction"].agg(lambda x: x.mode()[0]).reset_index()

    # For each question-answer pair, get the first occurrence's task and is_correct
    first_occurrences = (
        df.groupby(["question", "prediction"]).agg({"task": "first", "is_correct": "first"}).reset_index()
    )

    # Merge the mode answers with their corresponding first occurrences
    result = answer_modes.merge(first_occurrences, on=["question", "prediction"], how="left")

    return result


def oracle(df):
    def get_first_correct_or_first_wrong(group):
        correct_answers = group[group["is_correct"]]
        if len(correct_answers) > 0:
            return correct_answers.iloc[0]
        return group.iloc[0]

    result = df.groupby("question").apply(get_first_correct_or_first_wrong)

    return result.reset_index(drop=True)


display((long_series.groupby("agent_name")["is_correct"].mean() * 100).round(2))
print(f"Majority score: {majority_vote(long_series)['is_correct'].mean() * 100:.2f}")
print(f"Oracle score: {oracle(long_series)['is_correct'].mean() * 100:.2f}")

agent_name
code_gpt4o_03_february_goodoldtext-unbroken       38.36
code_gpt4o_03_february_magenticbrowser            35.22
code_gpt4o_03_february_magenticbrowser2           36.54
code_gpt4o_03_february_text                       37.58
code_o1_01_february_text                          49.09
code_o1_03_february_fix-print-outputs             51.83
code_o1_03_february_fix-print-outputs2            52.56
code_o1_03_february_goodoldtext-unbroken          53.42
code_o1_03_february_remove-navigational           53.66
code_o1_03_february_text_high-reasoning-effort    48.48
code_o3-mini_03_february_remove-navigational      29.09
Name: is_correct, dtype: float64

Majority score: 58.18
Oracle score: 70.91


/var/folders/6m/9b1tts6d5w960j80wbw9tx3m0000gn/T/ipykernel_94354/2283375871.py:25: DeprecationWarning:

DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.

